
[LivePortrait GitHub](https://github.com/KwaiVGI/LivePortrait) <br>
[Hugging Face Model Card](https://huggingface.co/KwaiVGI/LivePortrait/tree/main)<br>
[Hugging Face Space](https://huggingface.co/spaces/KwaiVGI/LivePortrait)



In [1]:
#@title Download Pretrained Weights and Install Packages
#for kaggle fix this line
%cd /content/
!rm -rf ./LivePortrait
!git clone https://github.com/KwaiVGI/LivePortrait.git

from tqdm import tqdm
import urllib
import os
import shutil
def conditional_download(url, download_file_path):
    print(f"Downloading {os.path.basename(download_file_path)}")
    base_path = os.path.dirname(download_file_path)

    if not os.path.exists(base_path):
        os.makedirs(base_path)

    if os.path.exists(download_file_path):
        os.remove(download_file_path)

    try:
        request = urllib.request.urlopen(url)  # type: ignore[attr-defined]
        total = int(request.headers.get('Content-Length', 0))
    except urllib.error.URLError as e:
        print(f"Error: Unable to open the URL - {url}")
        print(f"Reason: {e.reason}")
        return

    with tqdm(total=total, desc='Downloading', unit='B', unit_scale=True, unit_divisor=1024) as progress:
        try:
            urllib.request.urlretrieve(url, download_file_path, reporthook=lambda count, block_size, total_size: progress.update(block_size))  # type: ignore[attr-defined]
        except urllib.error.URLError as e:
            print(f"Error: Failed to download the file from the URL - {url}")
            print(f"Reason: {e.reason}")
            return

    print(f"Download successful!")
    print(f"URL: {url}")
    print(f"Save at: {download_file_path}")




def download_models(base_path):
    # Function to download files
    def download_files(file_list, relative_path, base_url):
        for file_name in file_list:
            download_file_path = f"{base_path}/{relative_path}/{file_name}"
            conditional_download(f"{base_url}/{file_name}", download_file_path)

    # Define file lists and paths
    buffalo_l_files = ["2d106det.onnx", "det_10g.onnx"]
    buffalo_l_path = "LivePortrait/pretrained_weights/insightface/models/buffalo_l"
    buffalo_l_url = "https://huggingface.co/KwaiVGI/LivePortrait/resolve/main/insightface/models/buffalo_l"

    base_models_files = [
        'appearance_feature_extractor.pth',
        'motion_extractor.pth',
        'spade_generator.pth',
        'warping_module.pth'
    ]
    base_models_path = "LivePortrait/pretrained_weights/liveportrait/base_models"
    base_models_url = "https://huggingface.co/KwaiVGI/LivePortrait/resolve/main/liveportrait/base_models"

    retargeting_models_files = ['stitching_retargeting_module.pth']
    retargeting_models_path = "LivePortrait/pretrained_weights/liveportrait/retargeting_models"
    retargeting_models_url = "https://huggingface.co/KwaiVGI/LivePortrait/resolve/main/liveportrait/retargeting_models"

    landmark_file = ["landmark.onnx"]
    landmark_path = "LivePortrait/pretrained_weights/liveportrait"
    landmark_url = "https://huggingface.co/KwaiVGI/LivePortrait/resolve/main/liveportrait"

    # Download files
    download_files(buffalo_l_files, buffalo_l_path, buffalo_l_url)
    download_files(base_models_files, base_models_path, base_models_url)
    download_files(retargeting_models_files, retargeting_models_path, retargeting_models_url)
    download_files(landmark_file, landmark_path, landmark_url)

#set up base_path
import os
root_path=os.getcwd()
# root_path="/content"
base_path=f"{root_path}"
#download model
download_models(base_path)
os.chdir(f"{base_path}/LivePortrait")
!pip install -r requirements.txt
from IPython.display import clear_output
clear_output()

In [2]:
#@title Run Gradio app
# coding: utf-8
%cd /content/LivePortrait
"""
The entrance of the gradio
"""

import tyro
import subprocess
import gradio as gr
import os.path as osp
from src.utils.helper import load_description
from src.gradio_pipeline import GradioPipeline
from src.config.crop_config import CropConfig
from src.config.argument_config import ArgumentConfig
from src.config.inference_config import InferenceConfig


def partial_fields(target_class, kwargs):
    return target_class(**{k: v for k, v in kwargs.items() if hasattr(target_class, k)})


def fast_check_ffmpeg():
    try:
        subprocess.run(["ffmpeg", "-version"], capture_output=True, check=True)
        return True
    except:
        return False


# set tyro theme
# tyro.extras.set_accent_color("bright_cyan")
# args = tyro.cli(ArgumentConfig)

###colab add code start
# Set default values for ArgumentConfig
default_args = {
    "server_name": "0.0.0.0",
    "server_port": 7860,
    "share": True,
    # Add other default values as needed
}

# Create an args object with default values
args = ArgumentConfig(**default_args)
###colab add code end

if not fast_check_ffmpeg():
    raise ImportError(
        "FFmpeg is not installed. Please install FFmpeg (including ffmpeg and ffprobe) before running this script. https://ffmpeg.org/download.html"
    )

# specify configs for inference
inference_cfg = partial_fields(InferenceConfig, args.__dict__)  # use attribute of args to initial InferenceConfig
crop_cfg = partial_fields(CropConfig, args.__dict__)  # use attribute of args to initial CropConfig
# global_tab_selection = None

gradio_pipeline = GradioPipeline(
    inference_cfg=inference_cfg,
    crop_cfg=crop_cfg,
    args=args
)


def gpu_wrapped_execute_video(*args, **kwargs):
    return gradio_pipeline.execute_video(*args, **kwargs)


def gpu_wrapped_execute_image(*args, **kwargs):
    return gradio_pipeline.execute_image(*args, **kwargs)


# assets
title_md = "assets/gradio/gradio_title.md"
example_portrait_dir = "assets/examples/source"
example_video_dir = "assets/examples/driving"
data_examples_i2v = [
    [osp.join(example_portrait_dir, "s9.jpg"), osp.join(example_video_dir, "d0.mp4"), True, True, True, False],
    [osp.join(example_portrait_dir, "s6.jpg"), osp.join(example_video_dir, "d0.mp4"), True, True, True, False],
    [osp.join(example_portrait_dir, "s10.jpg"), osp.join(example_video_dir, "d0.mp4"), True, True, True, False],
    [osp.join(example_portrait_dir, "s5.jpg"), osp.join(example_video_dir, "d18.mp4"), True, True, True, False],
    [osp.join(example_portrait_dir, "s7.jpg"), osp.join(example_video_dir, "d19.mp4"), True, True, True, False],
    [osp.join(example_portrait_dir, "s2.jpg"), osp.join(example_video_dir, "d13.mp4"), True, True, True, True],
]
data_examples_v2v = [
    [osp.join(example_portrait_dir, "s13.mp4"), osp.join(example_video_dir, "d0.mp4"), True, True, True, False, False, 1e-7],
    # [osp.join(example_portrait_dir, "s14.mp4"), osp.join(example_video_dir, "d18.mp4"), True, True, True, False, False, 1e-7],
    # [osp.join(example_portrait_dir, "s15.mp4"), osp.join(example_video_dir, "d19.mp4"), True, True, True, False, False, 1e-7],
    [osp.join(example_portrait_dir, "s18.mp4"), osp.join(example_video_dir, "d6.mp4"), True, True, True, False, False, 1e-7],
    # [osp.join(example_portrait_dir, "s19.mp4"), osp.join(example_video_dir, "d6.mp4"), True, True, True, False, False, 1e-7],
    [osp.join(example_portrait_dir, "s20.mp4"), osp.join(example_video_dir, "d0.mp4"), True, True, True, False, False, 1e-7],
]
#################### interface logic ####################

# Define components first
eye_retargeting_slider = gr.Slider(minimum=0, maximum=0.8, step=0.01, label="target eyes-open ratio")
lip_retargeting_slider = gr.Slider(minimum=0, maximum=0.8, step=0.01, label="target lip-open ratio")
retargeting_input_image = gr.Image(type="filepath")
output_image = gr.Image(type="numpy")
output_image_paste_back = gr.Image(type="numpy")
output_video_i2v = gr.Video(autoplay=False)
output_video_concat_i2v = gr.Video(autoplay=False)
# output_video_v2v = gr.Video(autoplay=False)
# output_video_concat_v2v = gr.Video(autoplay=False)


with gr.Blocks(theme=gr.themes.Soft(font=[gr.themes.GoogleFont("Plus Jakarta Sans")])) as demo:
    gr.HTML(load_description(title_md))

    gr.Markdown(load_description("assets/gradio/gradio_description_upload.md"))
    with gr.Row():
        with gr.Column():
            with gr.Tabs():
                with gr.TabItem("🖼️ Source Image") as tab_image:
                    with gr.Accordion(open=True, label="Source Image"):
                        source_image_input = gr.Image(type="filepath")
                        gr.Examples(
                            examples=[
                                [osp.join(example_portrait_dir, "s9.jpg")],
                                [osp.join(example_portrait_dir, "s6.jpg")],
                                [osp.join(example_portrait_dir, "s10.jpg")],
                                [osp.join(example_portrait_dir, "s5.jpg")],
                                [osp.join(example_portrait_dir, "s7.jpg")],
                                [osp.join(example_portrait_dir, "s12.jpg")],
                            ],
                            inputs=[source_image_input],
                            cache_examples=False,
                        )

                with gr.TabItem("🎞️ Source Video") as tab_video:
                    with gr.Accordion(open=True, label="Source Video"):
                        source_video_input = gr.Video()
                        gr.Examples(
                            examples=[
                                [osp.join(example_portrait_dir, "s13.mp4")],
                                # [osp.join(example_portrait_dir, "s14.mp4")],
                                # [osp.join(example_portrait_dir, "s15.mp4")],
                                [osp.join(example_portrait_dir, "s18.mp4")],
                                # [osp.join(example_portrait_dir, "s19.mp4")],
                                [osp.join(example_portrait_dir, "s20.mp4")],
                            ],
                            inputs=[source_video_input],
                            cache_examples=False,
                        )

                tab_selection = gr.Textbox(visible=False)
                tab_image.select(lambda: "Image", None, tab_selection)
                tab_video.select(lambda: "Video", None, tab_selection)
            with gr.Accordion(open=True, label="Cropping Options for Source Image or Video"):
                with gr.Row():
                    flag_do_crop_input = gr.Checkbox(value=True, label="do crop (source)")
                    scale = gr.Number(value=2.3, label="source crop scale", minimum=1.8, maximum=3.2, step=0.05)
                    vx_ratio = gr.Number(value=0.0, label="source crop x", minimum=-0.5, maximum=0.5, step=0.01)
                    vy_ratio = gr.Number(value=-0.125, label="source crop y", minimum=-0.5, maximum=0.5, step=0.01)

        with gr.Column():
            with gr.Accordion(open=True, label="Driving Video"):
                driving_video_input = gr.Video()
                gr.Examples(
                    examples=[
                        [osp.join(example_video_dir, "d0.mp4")],
                        [osp.join(example_video_dir, "d18.mp4")],
                        [osp.join(example_video_dir, "d19.mp4")],
                        [osp.join(example_video_dir, "d14.mp4")],
                        [osp.join(example_video_dir, "d6.mp4")],
                    ],
                    inputs=[driving_video_input],
                    cache_examples=False,
                )
            # with gr.Accordion(open=False, label="Animation Instructions"):
                # gr.Markdown(load_description("assets/gradio/gradio_description_animation.md"))
            with gr.Accordion(open=True, label="Cropping Options for Driving Video"):
                with gr.Row():
                    flag_crop_driving_video_input = gr.Checkbox(value=False, label="do crop (driving)")
                    scale_crop_driving_video = gr.Number(value=2.2, label="driving crop scale", minimum=1.8, maximum=3.2, step=0.05)
                    vx_ratio_crop_driving_video = gr.Number(value=0.0, label="driving crop x", minimum=-0.5, maximum=0.5, step=0.01)
                    vy_ratio_crop_driving_video = gr.Number(value=-0.1, label="driving crop y", minimum=-0.5, maximum=0.5, step=0.01)

    with gr.Row():
        with gr.Accordion(open=True, label="Animation Options"):
            with gr.Row():
                flag_relative_input = gr.Checkbox(value=True, label="relative motion")
                flag_remap_input = gr.Checkbox(value=True, label="paste-back")
                flag_video_editing_head_rotation = gr.Checkbox(value=False, label="relative head rotation (v2v)")
                driving_smooth_observation_variance = gr.Number(value=1e-7, label="motion smooth strength (v2v)", minimum=1e-11, maximum=1e-2, step=1e-8)

    gr.Markdown(load_description("assets/gradio/gradio_description_animate_clear.md"))
    with gr.Row():
        with gr.Column():
            process_button_animation = gr.Button("🚀 Animate", variant="primary")
        with gr.Column():
            process_button_reset = gr.ClearButton([source_image_input, source_video_input, driving_video_input, output_video_i2v, output_video_concat_i2v], value="🧹 Clear")
    with gr.Row():
        with gr.Column():
            with gr.Accordion(open=True, label="The animated video in the original image space"):
                output_video_i2v.render()
        with gr.Column():
            with gr.Accordion(open=True, label="The animated video"):
                output_video_concat_i2v.render()

    with gr.Row():
        # Examples
        gr.Markdown("## You could also choose the examples below by one click ⬇️")
    with gr.Row():
        with gr.Tabs():
            with gr.TabItem("🖼️ Portrait Animation"):
                gr.Examples(
                    examples=data_examples_i2v,
                    fn=gpu_wrapped_execute_video,
                    inputs=[
                        source_image_input,
                        driving_video_input,
                        flag_relative_input,
                        flag_do_crop_input,
                        flag_remap_input,
                        flag_crop_driving_video_input,
                    ],
                    outputs=[output_image, output_image_paste_back],
                    examples_per_page=len(data_examples_i2v),
                    cache_examples=False,
                )
            with gr.TabItem("🎞️ Portrait Video Editing"):
                gr.Examples(
                    examples=data_examples_v2v,
                    fn=gpu_wrapped_execute_video,
                    inputs=[
                        source_video_input,
                        driving_video_input,
                        flag_relative_input,
                        flag_do_crop_input,
                        flag_remap_input,
                        flag_crop_driving_video_input,
                        flag_video_editing_head_rotation,
                        driving_smooth_observation_variance,
                    ],
                    outputs=[output_image, output_image_paste_back],
                    examples_per_page=len(data_examples_v2v),
                    cache_examples=False,
                )

    # Retargeting
    gr.Markdown(load_description("assets/gradio/gradio_description_retargeting.md"), visible=True)
    with gr.Row(visible=True):
        eye_retargeting_slider.render()
        lip_retargeting_slider.render()
    with gr.Row(visible=True):
        process_button_retargeting = gr.Button("🚗 Retargeting", variant="primary")
        process_button_reset_retargeting = gr.ClearButton(
            [
                eye_retargeting_slider,
                lip_retargeting_slider,
                retargeting_input_image,
                output_image,
                output_image_paste_back
            ],
            value="🧹 Clear"
        )
    with gr.Row(visible=True):
        with gr.Column():
            with gr.Accordion(open=True, label="Retargeting Input"):
                retargeting_input_image.render()
                gr.Examples(
                    examples=[
                        [osp.join(example_portrait_dir, "s9.jpg")],
                        [osp.join(example_portrait_dir, "s6.jpg")],
                        [osp.join(example_portrait_dir, "s10.jpg")],
                        [osp.join(example_portrait_dir, "s5.jpg")],
                        [osp.join(example_portrait_dir, "s7.jpg")],
                        [osp.join(example_portrait_dir, "s12.jpg")],
                    ],
                    inputs=[retargeting_input_image],
                    cache_examples=False,
                )
        with gr.Column():
            with gr.Accordion(open=True, label="Retargeting Result"):
                output_image.render()
        with gr.Column():
            with gr.Accordion(open=True, label="Paste-back Result"):
                output_image_paste_back.render()

    # binding functions for buttons
    process_button_retargeting.click(
        # fn=gradio_pipeline.execute_image,
        fn=gpu_wrapped_execute_image,
        inputs=[eye_retargeting_slider, lip_retargeting_slider, retargeting_input_image, flag_do_crop_input],
        outputs=[output_image, output_image_paste_back],
        show_progress=True
    )
    process_button_animation.click(
        fn=gpu_wrapped_execute_video,
        inputs=[
            source_image_input,
            source_video_input,
            driving_video_input,
            flag_relative_input,
            flag_do_crop_input,
            flag_remap_input,
            flag_crop_driving_video_input,
            flag_video_editing_head_rotation,
            scale,
            vx_ratio,
            vy_ratio,
            scale_crop_driving_video,
            vx_ratio_crop_driving_video,
            vy_ratio_crop_driving_video,
            driving_smooth_observation_variance,
            tab_selection,
        ],
        outputs=[output_video_i2v, output_video_concat_i2v],
        show_progress=True
    )
##########################################################
# demo.launch(
#     server_port=args.server_port,
#     share=args.share,
#     server_name=args.server_name
# )
demo.launch(share=True)


/content


[13:14:36] Load appearance_feature_extractor done.                                      ]8;id=942416;file:///content/LivePortrait/src/live_portrait_wrapper.py\live_portrait_wrapper.py]8;;\:]8;id=660892;file:///content/LivePortrait/src/live_portrait_wrapper.py#40\40]8;;\

[13:14:37] Load motion_extractor done.                                                  ]8;id=394236;file:///content/LivePortrait/src/live_portrait_wrapper.py\live_portrait_wrapper.py]8;;\:]8;id=634963;file:///content/LivePortrait/src/live_portrait_wrapper.py#43\43]8;;\

[13:14:38] Load warping_module done.                                                    ]8;id=3087;file:///content/LivePortrait/src/live_portrait_wrapper.py\live_portrait_wrapper.py]8;;\:]8;id=356808;file:///content/LivePortrait/src/live_portrait_wrapper.py#46\46]8;;\

[13:14:39] Load spade_generator done.                                                   ]8;id=102975;file:///content/LivePortrait/src/live_portrait_wrapper.py\live_portrait_wrapper.py]8;;\:]8;id=669040;file:///content/LivePortrait/src/live_portrait_wrapper.py#49\49]8;;\

           Load stitching_retargeting_module done.                                      ]8;id=205677;file:///content/LivePortrait/src/live_portrait_wrapper.py\live_portrait_wrapper.py]8;;\:]8;id=518707;file:///content/LivePortrait/src/live_portrait_wrapper.py#53\53]8;;\

[13:14:42] LandmarkRunner warmup time: 1.928s                                                 ]8;id=25633;file:///content/LivePortrait/src/utils/landmark_runner.py\landmark_runner.py]8;;\:]8;id=818913;file:///content/LivePortrait/src/utils/landmark_runner.py#95\95]8;;\

[13:14:44] FaceAnalysisDIY warmup time: 1.397s                                              ]8;id=818885;file:///content/LivePortrait/src/utils/face_analysis_diy.py\face_analysis_diy.py]8;;\:]8;id=486391;file:///content/LivePortrait/src/utils/face_analysis_diy.py#79\79]8;;\

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
Running on public URL: https://10b29a04ae6ffe05bf.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)


## Without Gradio App

In [6]:
#@title Utils
from google.colab import files
import re
import os
import uuid
from IPython.display import clear_output

def clean_file_name(file_path):
  # Get the base file name and extension
  file_name = os.path.basename(file_path)
  file_name, file_extension = os.path.splitext(file_name)
  cleaned = re.sub(r'[^a-zA-Z\d]+', '_', file_name)   # Replace non-alphabetic characters with single underscore
  clean_file_name=re.sub(r'([a-zA-Z])_+([a-zA-Z])', r'\1_\2', cleaned)  # Replace multiple underscores between alphabets with one underscore
  clean_file_name = clean_file_name.strip('_')
  random_uuid = uuid.uuid4().hex[:6]
  # Combine cleaned file name with the original extension
  clean_file_path = os.path.join(os.path.dirname(file_path), clean_file_name +f"_{random_uuid}"+file_extension)
  return clean_file_path


def upload_image():
  upload_folder="/content/LivePortrait/user_upload"
  if not os.path.exists(upload_folder):
    os.mkdir(upload_folder)
  os.chdir(upload_folder)
  uploaded = files.upload()
  os.chdir("/content/LivePortrait")
  image_name_list=[]
  for fn in uploaded.keys():
    file_path=f"{upload_folder}/{fn}"
    save_file_path=clean_file_name(file_path)
    os.rename(file_path,save_file_path)
    image_name_list.append(save_file_path)
  image_extensions = ('.png', '.jpg', '.jpeg')
  clear_output()
  for i in image_extensions:
    if image_name_list[-1].lower().endswith(i):
      return image_name_list[-1]
  else:
    print("Upload an Image")
  return None

import os
from google.colab import files
def upload_video():
  upload_folder="/content/LivePortrait/user_upload"
  if not os.path.exists(upload_folder):
    os.mkdir(upload_folder)
  os.chdir(upload_folder)
  uploaded = files.upload()
  os.chdir("/content/LivePortrait")
  clear_output()
  video_name_list=[]
  for fn in uploaded.keys():
    file_path=f"{upload_folder}/{fn}"
    save_file_path=clean_file_name(file_path)
    os.rename(file_path,save_file_path)
    video_name_list.append(save_file_path)
  if video_name_list[-1].lower().endswith(".mp4"):
    return video_name_list[-1]
  else:
    print("Upload .mp4 Format Video")
  return None


def get_output_video(image_path,video_path):
  #extract base name only
  image_name=os.path.basename(image_path)
  video_name=os.path.basename(video_path)
  #only the filename without extention
  image_name=os.path.splitext(image_name)[0]
  video_name=os.path.splitext(video_name)[0]
  video_path=f"{image_name}--{video_name}.mp4"
  concat_video_path=f"{image_name}--{video_name}_concat.mp4"
  return video_path,concat_video_path

def LivePortrait_video_maker(Image_Path,Reference_Video_Path):
  global base_path
  save_folder=f"{base_path}/generated_clips"
  if os.path.exists(save_folder):
    shutil.rmtree(save_folder)

  if os.getcwd() != f"{base_path}/LivePortrait":
    os.chdir(f"{base_path}/LivePortrait")
  command=f"python inference.py -s {Image_Path} -d {Reference_Video_Path}  -o {save_folder} --flag_crop_driving_video"
  var=os.system(command)
  if var==0:
    video_path,concat_video_path=get_output_video(Image_Path,Reference_Video_Path)
    output_video=f"{save_folder}/{video_path}"
    concat_video=f"{save_folder}/{concat_video_path}"
    return output_video,concat_video
  else:
    print(f"Error")
    print(command)
    return None

from IPython.display import HTML
from base64 import b64encode

def show_video(video_path, video_width = 600):

  video_file = open(video_path, "r+b").read()

  video_url = f"data:video/mp4;base64,{b64encode(video_file).decode()}"
  return HTML(f"""<video width={video_width} controls><source src="{video_url}"></video>""")

# Image to Video

In [ ]:
#@title Upload Image
uploaded_image_path=upload_image()

uploaded_image_path

'/content/LivePortrait/user_upload/Girl_f5b7f2.jpeg'

In [ ]:
#@title Upload Video
uploaded_video_path=upload_video()
uploaded_video_path

'/content/LivePortrait/user_upload/d0_bee717.mp4'

In [ ]:
#@title Run LivePortrait AI for Image to Video
Image_Path = '/content/LivePortrait/user_upload/Girl_f5b7f2.jpeg'  # @param {type: "string"}
Reference_Video_Path = '/content/LivePortrait/user_upload/d0_bee717.mp4'  # @param {type: "string"}
output_video,concat_video=LivePortrait_video_maker(Image_Path,Reference_Video_Path)
print(f"Video save at {output_video}")
from google.colab import files
files.download(output_video)
files.download(concat_video)

Video save at /content/generated_clips/Girl_f5b7f2--d0_bee717.mp4


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
#@title Display Generated  Video
show_video(output_video, video_width = 600)


In [ ]:
#@title Before and After Comparison Video
show_video(concat_video, video_width = 600)

In [ ]:
#@title Download Again (if Google Chrome blocked the duplicate download)
from google.colab import files
files.download(output_video)
files.download(concat_video)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## Video to Video

In [4]:
#@title Upload Source Video
source_video_path=upload_video()
source_video_path

'/content/LivePortrait/user_upload/s20_0bdfc5.mp4'

In [5]:
#@title Upload Driving Video
driving_video_path=upload_video()
driving_video_path

'/content/LivePortrait/user_upload/d14_a296b0.mp4'

In [8]:
#@title Run LivePortrait AI for Image to Video
Source_Video_Path = '/content/LivePortrait/user_upload/s20_0bdfc5.mp4'  # @param {type: "string"}
Driving_Video_Path = '/content/LivePortrait/user_upload/d14_a296b0.mp4'  # @param {type: "string"}
output_video_,concat_video_=LivePortrait_video_maker(Source_Video_Path,Driving_Video_Path)
print(f"Video save at {output_video_}")
from google.colab import files
files.download(output_video_)
files.download(concat_video_)

Video save at /content/generated_clips/s20_0bdfc5--d14_a296b0.mp4


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [9]:
#@title Display Generated  Video
show_video(output_video_, video_width = 600)

In [10]:
#@title Before and After Comparison Video
show_video(concat_video_, video_width = 600)

In [11]:
#@title Download Again (if Google Chrome blocked the duplicate download)
from google.colab import files
files.download(output_video_)
files.download(concat_video_)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>